## Song Metadata DB 

#### Found Here: https://song-metadata-default-rtdb.firebaseio.com/

Purpose: To store basic information about each track, useful for general queries and indexing.

Columns / Variables : track_id, artists, album_name, track_name, popularity, duration_ms, explicit, track_genre.

 

##  Audio Elements DB

#### Found Here: https://audio-elements-e5904-default-rtdb.firebaseio.com/

Purpose: To store detailed audio features of each song, useful for analysis and recommendation algorithms.

Columns/ Variables : track_id, danceability, energy, key, loudness, mode, speechiness, acousticness, instrumentalness, liveness, valence, tempo, time_signature.

In [2]:
#requirements
pip install firebase-admin

     |████████████████████████████████| 120 kB 746 kB/s eta 0:00:01
     |████████████████████████████████| 121 kB 6.1 MB/s eta 0:00:01
     |████████████████████████████████| 137 kB 12.2 MB/s eta 0:00:01
     |████████████████████████████████| 290 kB 34.7 MB/s eta 0:00:01
     |████████████████████████████████| 12.1 MB 58.2 MB/s eta 0:00:01
     |████████████████████████████████| 96 kB 9.2 MB/s  eta 0:00:01
     |████████████████████████████████| 48 kB 24.2 MB/s eta 0:00:01
     |████████████████████████████████| 80 kB 33.9 MB/s eta 0:00:01
     |████████████████████████████████| 186 kB 145.1 MB/s eta 0:00:01
     |████████████████████████████████| 9.7 MB 20.6 MB/s eta 0:00:01
  Attempting uninstall: grpcio
    Found existing installation: grpcio 1.49.1
    Uninstalling grpcio-1.49.1:
      Successfully uninstalled grpcio-1.49.1
  Attempting uninstall: google-auth
    Found existing installation: google-auth 2.17.3
    Uninstalling google-auth-2.17.3:
      Successfully uninstalled go

In [1]:
#Import Libraries/Modules
import os
import pandas as pd
import firebase_admin
from firebase_admin import credentials, db

In [2]:
#Load data
file_path = 'spotify_data.csv'
spotify_data = pd.read_csv(file_path)

#Split the data into two DF's
song_metadata_cols = ['track_id', 'artists', 'album_name', 'track_name', 'track_genre']
audio_elements_cols = ['track_id', 'popularity', 'danceability', 'energy', 'key', 'loudness', 'mode', 'speechiness', 'acousticness', 'instrumentalness', 'liveness', 'valence', 'tempo', 'time_signature']

#Assign new Df's
song_metadata = spotify_data[song_metadata_cols]
audio_elements = spotify_data[audio_elements_cols]


## Instructions to find or generate the JSON Firebase DB Key file:

1. Go to the Firebase Console: Visit Firebase Console and select your project.

2. Access Project Settings: Click on the gear icon next to "Project Overview" in the sidebar and select "Project settings."

3. Navigate to Service Accounts: In the project settings, go to the "Service accounts" tab.

4. Generate a New Private Key: Click on the "Generate new private key" button. A JSON file will be downloaded to your computer.

5. The path you need to provide in the script is the location where this JSON file is saved

## On macOS or Linux, use the export command in the terminal: 


### Option 1:
export SONG_METADATA_CREDENTIALS=path/to/song_metadata_credentials.json

export AUDIO_ELEMENTS_CREDENTIALS=path/to/audio_elements_credentials.json

### Option 2:

Set the os variabels directly in the environment using  'os.environ'.  Replace path\to\song_metadata_credentials.json and path\to\audio_elements_credentials.json with the actual paths to your own credentials files.

Each collaborator can set these environment variables on their own machine, ensuring that sensitive information is kept secure and out of version control.



In [5]:
os.environ['SONG_METADATA_CREDENTIALS'] = 'YOUR PATH TO YOU JSON FILE KEYS TO THE SPECIFIC SONG META DATA DATABASE'

os.environ['AUDIO_ELEMENTS_CREDENTIALS'] = 'YOUR PATH TO YOU JSON FILE KEYS TO THE SPECIFIC AUDIO ELEMENTS DATABASE'

In [6]:
#Initialize Firebase Admin SDK for both databases using environment variables
cred_song_metadata = credentials.Certificate(os.environ.get('SONG_METADATA_CREDENTIALS'))
firebase_admin.initialize_app(cred_song_metadata, {
    'databaseURL': 'https://song-metadata-default-rtdb.firebaseio.com/'
}, name='song_metadata')

cred_audio_elements = credentials.Certificate(os.environ.get('AUDIO_ELEMENTS_CREDENTIALS'))
firebase_admin.initialize_app(cred_audio_elements, {
    'databaseURL': 'https://audio-elements-e5904-default-rtdb.firebaseio.com/'
}, name='audio_elements')



In [11]:
def upload_data_to_firebase(df, db_url, db_name):
    ref = db.reference('/', app=firebase_admin.get_app(db_name))
    for index, row in df.iterrows():
        #convert the row to a dictionary and replace NaN and infinite values
        row_dict = row.to_dict()
        for key, value in row_dict.items():
            if pd.isna(value) or value in [float('inf'), float('-inf')]:
                row_dict[key] = None  # replace with None or a suitable value

        #check if the record already exists, so we do not upload duplicate songs
        track_id = str(row['track_id'])
        if ref.child(track_id).get() is None:
            ref.child(track_id).set(row_dict)
        else:
            print(f"Skipping existing record: {track_id}")


In [12]:
#Upload song metadata to Firebase 
upload_data_to_firebase(song_metadata, 'https://song-metadata-default-rtdb.firebaseio.com/', 'song_metadata')


Skipping existing record: 5SuOikwiRyPMVoIQDJUgSV
Skipping existing record: 4qPNDBW1i3p13qLCt0Ki3A
Skipping existing record: 1iJBSr7s7jYXzM8EGcbK5b
Skipping existing record: 6lfxq3CG4xtTiEg7opyCyx
Skipping existing record: 5vjLSffimiIP26QG5WcN2K
Skipping existing record: 01MVOl9KtVTNfFiBU9I7dc
Skipping existing record: 6Vc5wAMmXdKIAM7WUoEb7N
Skipping existing record: 1EzrEOXmMH3G43AXT1y7pA
Skipping existing record: 0IktbUcnAGrvD03AWnz3Q8
Skipping existing record: 7k9GuJYLp2AzqokyEdwEw2
Skipping existing record: 4mzP5mHkRvGxdhdGdAH7EJ
Skipping existing record: 5ivF4eQBqJiVL5IAE9jRyl
Skipping existing record: 4ptDJbJl35d7gQfeNteBwp
Skipping existing record: 0X9MxHR1rTkEHDjp95F2OO
Skipping existing record: 4LbWtBkN82ZRhz9jqzgrb3
Skipping existing record: 1KHdq8NK9QxnGjdXb55NiG
Skipping existing record: 6xKeQgzfjixSUld14qUezm
Skipping existing record: 4Yo0igmcoNyat1secaH0OD
Skipping existing record: 2qLMf6TuEC3ruGJg4SMMN6
Skipping existing record: 6CgNoAbFJ4Q4Id4EjtbXlC
Skipping existing re

Skipping existing record: 3tob5ofeuvFKKSbOTldenC
Skipping existing record: 4E6cwWJWZw2zWf7VFbH7wf
Skipping existing record: 3uAdZpIbMTtVXitHVibLMV
Skipping existing record: 2LC523tbEPFpc1pnikbt5b
Skipping existing record: 3ISLwA96mtx13Wx7K1PPPk
Skipping existing record: 7Ca2CkwSqHyr3eCh8IRdjz
Skipping existing record: 6ql0ffq6Jvyh9OKqrJCMaP
Skipping existing record: 1EyvonxK8OGHRV4WDRdArc
Skipping existing record: 0EKBV6GybPtALXUgWqWrym
Skipping existing record: 41A82PidFKhGX5hm1WoaDs
Skipping existing record: 5oV8bZaShr2d01FFMHBUPq
Skipping existing record: 5nMRpGfqQ0tb1TMbqBVK2J
Skipping existing record: 04qDUASuSfVp6fktfsxVej
Skipping existing record: 3g61xRaqII8q1wlQDzv550
Skipping existing record: 3dglCYsVMjPbDlU2CC9Vq7
Skipping existing record: 2f4jlGvGi3ZDGogXys5FUp
Skipping existing record: 3NCg46FWgnANZc9HQHQOQR
Skipping existing record: 0muntSMuAZzcwYBBMZj6sf
Skipping existing record: 4bXoVtbp6fN8FaSQvGQB41
Skipping existing record: 3FRARAKLpHw3er9ZaTwaHO
Skipping existing re

Skipping existing record: 5PoaNLRYLL7rywHSPUOZs8
Skipping existing record: 6DwgZO7AMYelPFwr8WPhpg
Skipping existing record: 5X3w2MfxgMTZkn2mTPQs0u
Skipping existing record: 5PCwedwyeLZQ6xAUIKbwos
Skipping existing record: 32kyGOJpEOTFKR9wvPSsxJ
Skipping existing record: 0ifc4mq2mVNefgQFmtXQpt
Skipping existing record: 2gJ3ZOaiWr3jGHwevufOxr
Skipping existing record: 37jsciEAFxwyjXx0kV6aO6
Skipping existing record: 22KbVMZekQbkrHGrubQTpQ
Skipping existing record: 4RiKD76gS8huCzwWqw0EGC
Skipping existing record: 3XFhSbm8EdZD6Cjrm1dNJQ
Skipping existing record: 3nImoHhXBOqYcdTN8gt9eE
Skipping existing record: 0B3g35bVxJ42Y0W0I5WBIU
Skipping existing record: 1igSa6QILI1jyE970ZMYW1
Skipping existing record: 4AYITlwiumljGdv0NIGR4T
Skipping existing record: 3YvutLE6lwEyW4WMF5FIi6
Skipping existing record: 3geIJghtdmVc7GeJio1xlj
Skipping existing record: 1yycinn2WICj4UKGQ9xPjD
Skipping existing record: 5Z8O4RFAmjA13jrOYIgyXA
Skipping existing record: 1ABd3bWsG4FCKePjXeVfJG
Skipping existing re

Skipping existing record: 4ISCO9MWDxOuteeVAm2ZWh
Skipping existing record: 6YOOCjjIb0pBZXbJjYgUlP
Skipping existing record: 1i7JnFAxC15AuF1dsosbYM
Skipping existing record: 7JY9axEOxQbeAN8OzwsOwy
Skipping existing record: 0eyE0L7FbNrXaByFzMXT1C
Skipping existing record: 0MY3K86lZ9HIat4oBi40dh
Skipping existing record: 16x2V0ZWoXD7Rjo6bSAoEK
Skipping existing record: 0zANeX4R6uWb82gCQAguOD
Skipping existing record: 3BztDPhRhfwdwUndTlg45h
Skipping existing record: 27hFQQS3cVUmIK3ser5bpu
Skipping existing record: 63F2nWghdifkNHVns5GT8W
Skipping existing record: 76w967eCBrUFBSzef2ExlK
Skipping existing record: 4kXcndvaQEROosxdcbJqzK
Skipping existing record: 0lczO04vbk2ZiNvAqzUUQ0
Skipping existing record: 6Fomnvc3pkLvUQYUkhiQPx
Skipping existing record: 6cMzeng5QA8fd2qqiMeIyg
Skipping existing record: 4jK6bBO2JbkvvgT7FPj8c5
Skipping existing record: 2jHEySxCzzODFWmPzt084L
Skipping existing record: 4XlevPQOF6GkZCS2yWOkNn
Skipping existing record: 4muAobUpgKTEgqskgNESmC
Skipping existing re

Skipping existing record: 3tInTDUq8wdIMw5ftohmqJ
Skipping existing record: 6Vn8lTVMjILXQCjZUXS8n4
Skipping existing record: 5hCgm1tDb7ZZKmRtucTTjh
Skipping existing record: 1PEpGWRE4Tjsk2qy5teW4p
Skipping existing record: 02EqvposhJjwrgkQexKIdW
Skipping existing record: 68HbD7rEFTlnJy4UWSpySY
Skipping existing record: 0qAMjeQFyd1qD0LDiV8gWp
Skipping existing record: 6b4mWoXrscyajbLOB2qwfG
Skipping existing record: 2C3gh14oarzTtv3aY3HJ0m
Skipping existing record: 2Qj1FilGsXITZbFVmVeoLy
Skipping existing record: 2gc1XwdI3kKipqAXTdMcwY
Skipping existing record: 35RrDnREM1xxx4YBxDHikm
Skipping existing record: 5bqPeBYkNk9feimSN9N4JY
Skipping existing record: 4a7aKxh344UzFEVd0k5lwi
Skipping existing record: 0P0v83waDX4ElzSgmF1cG5
Skipping existing record: 0NkeEkDFOby5xOZ7BIKVuD
Skipping existing record: 348ooLg3LgeDkJVh6zzib8
Skipping existing record: 2BdXf4OpDOw4AvklnAvcsY
Skipping existing record: 6i1wlqIigKZTvMk0LTh5Id
Skipping existing record: 5CU7ewecONNlWAJHu04HJQ
Skipping existing re

...

Skipping existing record: 0VpW9XAE5QC0nj4qhQ4FGM
Skipping existing record: 2BIzYGq1Pyv5SLWEQbgNM4
Skipping existing record: 6I8FUsqR02Wh3SNhlOEc6y
Skipping existing record: 5yNn7FM82L2iaTQY0qkCF0
Skipping existing record: 61aw1V0KLPD4XIjqNsGqo9
Skipping existing record: 3tw38CkaOgncThUwXO80NO
Skipping existing record: 6L2B0EWlWnHR0YzLCmDgYh
Skipping existing record: 0MCmBvjVa6Jzo1az3uWghV
Skipping existing record: 1ZQYtiSmHLT1aiPDsIjvGn
Skipping existing record: 75CAWvWD9ATXlcPHhD7qp9
Skipping existing record: 5XxFY11r0YA6Xoyh1O9WsR
Skipping existing record: 34Bo1NPm9TdCsSUMfCxCTD
Skipping existing record: 15lzXkV36tS2YA5RIUK6JX
Skipping existing record: 5CI4uc5U66KH9g4nklN2JO
Skipping existing record: 5EbTHYIQQtNNMloPNirkKi
Skipping existing record: 6RNUCOPGtGF2qrzr5I3DE4
Skipping existing record: 1W8uXzcf0k3pFDnwqAiDY2
Skipping existing record: 5mLllF9AIePVdhExTiNyyr
Skipping existing record: 6cYJBIE9FC1QAoPw5EhdLA
Skipping existing record: 0xTsllHxzqwYrsPUcruf72
Skipping existing re

Skipping existing record: 6naCXLqx0qvSnYWkrbioFm
Skipping existing record: 6UNwFoIOo6SPYAP6pBRF2h
Skipping existing record: 0A5mmNP2Lk8mfCJjWWQvz7
Skipping existing record: 7bJIb0bPGNHq1RqO2ofA8v
Skipping existing record: 1QrxggFof36TcpeREbDAXI
Skipping existing record: 769LjA468VL4j2g4WI48Oe
Skipping existing record: 29KHMaejJLd64hc2FBfdSo
Skipping existing record: 5Pj8qBEzA9i0vK6Wdt889w
Skipping existing record: 13YWp1iozoy7YACZsRqRnK
Skipping existing record: 59s4wikOZ2H0YpHVz9Bfsu
Skipping existing record: 5k8kM7FMh07pr7R97VR7SY
Skipping existing record: 3YJIq3N5IQy1hhkmUnt2NM
Skipping existing record: 2Eu5IxBvLxCd1HFVR4JbR4
Skipping existing record: 4FpawvuBz4HxTz7UqR4ter
Skipping existing record: 3HywI2jpMgC8CO2bfjluN2
Skipping existing record: 5VyVQuqtPkKZt1jaXKuQkR
Skipping existing record: 4UKgwHcyWjHOeUIjixdyTj
Skipping existing record: 0YJogBxgISDK5cTI0U6dX1
Skipping existing record: 1tPRFD05l5FktbHf3qCzGe
Skipping existing record: 0CEgZkZWsT4tDNj15BX1fY
Skipping existing re

Skipping existing record: 4eO3uE6IJVbT5Xex1DrmbE
Skipping existing record: 3wvo6Fh3RBn5t60p3iK16Z
Skipping existing record: 0LCNtzhgRDbCpcfMAWL61u
Skipping existing record: 2Roub2Oj45R0903dCNZ1eh
Skipping existing record: 2DnINK9YPAgEpT9hP5cWqc
Skipping existing record: 2YYVPeCDpnCKo7mMnY4T4m
Skipping existing record: 7GXsxXkvOvSN8qyOtidFDQ
Skipping existing record: 3keynY7XZqJtdRZVnnLRKc
Skipping existing record: 5xKGdGXYh3LRYTzwVZSb0u
Skipping existing record: 5hlzz0D0ttrhZk8XSbbBVC
Skipping existing record: 2sscCAOTZOYW5N8MlNKbyQ
Skipping existing record: 5LXaBBZePqShzKxM6b9RFU
Skipping existing record: 0XMl0fVTh3PyPlwyJTn33n
Skipping existing record: 1bxtePWzYybaPiUZqvgQVf
Skipping existing record: 5Ss7C8bSDZMm0pt9pXqObC
Skipping existing record: 5sqkarfxe7UejHTlCtHCLS
Skipping existing record: 3YOZWCREvKsxhcZNJix5xd
Skipping existing record: 6UiDiFJUGEDzkGpZBL8IYq
Skipping existing record: 50yvBhmvDKCpc7Yzwobew6
Skipping existing record: 2wxs5sF8JzScf1CV8u9tNU
Skipping existing re

Skipping existing record: 7IgA0pcFcslMMsBZsDnWaX
Skipping existing record: 4RdZfdkgW1OmkajhvcOxA1
Skipping existing record: 0rSpu20UCvDF2BE2tNx4LF
Skipping existing record: 2L2rzhnx1Xr6LiGuaYMepY
Skipping existing record: 22szgJ9WufVHgefSgOD6Dv
Skipping existing record: 7hCZVX8ogwzgszIKtkD6Bv
Skipping existing record: 6AkEP2vEcpTRn2ilHVPNsa
Skipping existing record: 0onLNYV4aYuSQb8wPxR0O0
Skipping existing record: 1B0FEDRzzN5GP7HGZZfNQl
Skipping existing record: 56DeYl4hyvAQzi1CzD17zB
Skipping existing record: 7g8dJIEhLLS17rESlJbp1e
Skipping existing record: 2wfHc3wJjCeaaB78MlIJ2i
Skipping existing record: 3nbnyZb8F60d9vHLm8RX9N
Skipping existing record: 4tGJ68OwrbEobOLzyqsv1V
Skipping existing record: 27nGU2v3syK7aU3AVY2vUO
Skipping existing record: 63vjnB6EeQuVf64zLxIo90
Skipping existing record: 7JP8lWYrxpA8luKU8IPd3Y
Skipping existing record: 0pMqxVqhkyRGPeeNqgsLS8
Skipping existing record: 0tWAGWvw3WWySN5fXfW1jO
Skipping existing record: 5VVaoVH3Hj0PlhzifnQuAy
Skipping existing re

Skipping existing record: 26g90nfKw79y5ZcRRqHLCz
Skipping existing record: 5gFfoZxgMHgMiArpO4Balz
Skipping existing record: 1vZDPEngmDv3qxXQpVzuN6
Skipping existing record: 4PdRmauZ4AF8HJiwpMVaXT
Skipping existing record: 171luCSfSTBnaIVnfTVbS6
Skipping existing record: 4nGy2XA9QGxYb90cNyHguO
Skipping existing record: 062WEhWJ0tNa0CaAEuMwYB
Skipping existing record: 6TiiDZgtQ3xJLWzrGBWDmc
Skipping existing record: 4pbMu6fRhg9mEZcHaO4NNo
Skipping existing record: 39BYcHLXEyVRZ3WBlaUa6E
Skipping existing record: 6evqur3UoNFDzJp3eY86dq
Skipping existing record: 3soQ0e19kGGF6CDyCoZvrt
Skipping existing record: 0JZv3A589Gt4wFSHxOYWxq
Skipping existing record: 577q8gGSTryRxX1YHWSjWk
Skipping existing record: 4RNuCCsvfGF03sfmboHwlT
Skipping existing record: 12SNxpytVKahQ25nOTpbFX
Skipping existing record: 3qeXSz02VoeNntvBX0Skw6
Skipping existing record: 1smXC6H0O8po3P4bS7MrgC
Skipping existing record: 2FU1YUBRONE4XXTiffe2Bv
Skipping existing record: 5eI11836uL4Ek3jGS1p50y
Skipping existing re

In [10]:
# Upload audio elements to Firebase
upload_data_to_firebase(audio_elements, 'https://audio-elements-e5904-default-rtdb.firebaseio.com/', 'audio_elements')

### The END! 